In [0]:
 

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):

  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])


  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)


  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)


  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)


  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])


  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)


  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {

      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)


if __name__ == "__main__":
  tf.app.run()

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f06d2a478d0>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
I

INFO:tensorflow:probabilities = [[0.99991286 0.         0.00001737 0.00000016 0.00000004 0.00000773
  0.00006155 0.         0.00000003 0.00000019]
 [0.00000009 0.00000035 0.0000047  0.9996748  0.         0.00019054
  0.         0.00000019 0.00011335 0.00001599]
 [0.9990004  0.00000231 0.00071147 0.00000976 0.00000073 0.00013243
  0.00007718 0.00000304 0.00000685 0.00005589]
 [0.00015649 0.00000732 0.00042972 0.00003595 0.86171573 0.00027345
  0.00666865 0.00077239 0.12387442 0.00606578]
 [0.00000625 0.00000006 0.00000046 0.00008723 0.00000101 0.9996885
  0.00000006 0.0000034  0.00015177 0.00006126]
 [0.00065544 0.000173   0.05942193 0.00576502 0.0000162  0.00022659
  0.00055759 0.00000097 0.9331655  0.00001777]
 [0.00000973 0.00001194 0.00002103 0.0000206  0.99017113 0.00048727
  0.0001106  0.00013811 0.00018917 0.00884052]
 [0.00000211 0.00000427 0.0000887  0.00000081 0.0001193  0.0009271
  0.9977767  0.         0.00107735 0.00000371]
 [0.00000975 0.00000079 0.00000531 0.00000003 0.00

INFO:tensorflow:probabilities = [[0.00060202 0.01600559 0.00110752 0.00255388 0.025174   0.04639715
  0.00002252 0.81845164 0.01252268 0.07716303]
 [0.00000395 0.01117813 0.91985315 0.05046745 0.00016688 0.00008171
  0.00005898 0.00667833 0.01148025 0.0000312 ]
 [0.02412507 0.00121966 0.00084419 0.02110979 0.00011902 0.9254425
  0.00503215 0.00022772 0.01952325 0.00235657]
 [0.00000503 0.00000401 0.00001141 0.00022536 0.00353894 0.00003146
  0.00000017 0.00280767 0.00018859 0.9931873 ]
 [0.00186563 0.00000389 0.99679404 0.00097553 0.00000226 0.00011847
  0.00002662 0.00002785 0.00018038 0.00000532]
 [0.00053804 0.00028383 0.00128519 0.979202   0.00004735 0.00131727
  0.00000224 0.01366617 0.00265635 0.0010015 ]
 [0.00000252 0.00000527 0.00009686 0.00054348 0.00000044 0.00004526
  0.         0.9937057  0.00000122 0.00559922]
 [0.1245807  0.00017411 0.02885418 0.00501685 0.00000082 0.00170346
  0.00173835 0.00010654 0.83778834 0.00003661]
 [0.00000001 0.00000005 0.00000007 0.00000004 0.9

INFO:tensorflow:probabilities = [[0.00000837 0.00004497 0.00010026 0.99926573 0.00000324 0.00005131
  0.00000031 0.00000182 0.00046418 0.00005976]
 [0.00067893 0.00016955 0.00103043 0.00037491 0.7532487  0.00020339
  0.00012324 0.10897572 0.00099435 0.13420083]
 [0.00002433 0.40347505 0.00085909 0.00100823 0.01320709 0.01158298
  0.5498835  0.0000064  0.01986917 0.00008412]
 [0.00016421 0.00000868 0.00003584 0.00011793 0.00039788 0.00022628
  0.00006167 0.00000718 0.97883165 0.02014866]
 [0.00000019 0.0000011  0.00000098 0.00000628 0.9803137  0.00117932
  0.00000535 0.00013653 0.00010986 0.01824666]
 [0.9959869  0.00000144 0.00041495 0.00001525 0.00000008 0.00051304
  0.00000971 0.00004032 0.00286494 0.00015339]
 [0.00000413 0.99796474 0.0000083  0.00023063 0.00010838 0.00000321
  0.00000025 0.00078704 0.000293   0.0006003 ]
 [0.00005356 0.00073649 0.00319335 0.01940352 0.00181847 0.00120221
  0.0000714  0.00011023 0.9683431  0.00506772]
 [0.00001333 0.00000007 0.00000402 0.00054736 0.

INFO:tensorflow:probabilities = [[0.00789191 0.00021502 0.06179194 0.008945   0.21121408 0.00136027
  0.00137617 0.01634723 0.00463783 0.68622065]
 [0.00000166 0.00000295 0.999897   0.00008786 0.00000014 0.00000001
  0.00000055 0.0000098  0.00000005 0.        ]
 [0.00006957 0.00001055 0.0016837  0.00048375 0.00022882 0.02016596
  0.00122142 0.00000135 0.9761193  0.0000156 ]
 [0.00000823 0.9703921  0.00001819 0.00006674 0.0002824  0.00071433
  0.00005261 0.0010723  0.0272634  0.00012966]
 [0.00103387 0.00051813 0.9828476  0.00764361 0.00055208 0.0000206
  0.0013786  0.00032775 0.00565426 0.00002351]
 [0.00000807 0.00117238 0.9982236  0.00038887 0.00000036 0.00001946
  0.00005627 0.00000043 0.00013054 0.        ]
 [0.00000772 0.00000157 0.00000051 0.00106306 0.00000471 0.99410594
  0.00000036 0.00002077 0.00001217 0.00478319]
 [0.00000444 0.00213252 0.00011144 0.00120344 0.9472338  0.00104438
  0.00024074 0.00096947 0.01113268 0.03592713]
 [0.00000926 0.00002217 0.00027468 0.997511   0.0

...

INFO:tensorflow:probabilities = [[0.00025228 0.30012167 0.00396385 0.00089256 0.01062513 0.00010014
  0.000158   0.00069784 0.49767306 0.18551542]
 [0.         0.00000006 0.00001282 0.00002815 0.00000002 0.
  0.         0.9998977  0.00000125 0.00006004]
 [0.00000161 0.0000506  0.99924076 0.00001413 0.         0.
  0.00000003 0.00000004 0.00069283 0.        ]
 [0.00005161 0.01159176 0.00061598 0.98207456 0.00002569 0.00473547
  0.00003412 0.00004311 0.00032034 0.00050737]
 [0.99999297 0.00000055 0.00000267 0.00000002 0.00000009 0.00000034
  0.00000094 0.00000174 0.00000014 0.00000044]
 [0.00000006 0.00000006 0.00000057 0.00002948 0.         0.999938
  0.00002026 0.         0.00001152 0.00000002]
 [0.9989145  0.00000037 0.0001885  0.00002687 0.00000166 0.00002089
  0.00024797 0.00000133 0.00056995 0.00002801]
 [0.00000276 0.00001538 0.00125745 0.03353884 0.00000604 0.00032905
  0.00001979 0.00000042 0.96480966 0.00002061]
 [0.00000605 0.00000001 0.00000036 0.00140928 0.00000009 0.997785


INFO:tensorflow:probabilities = [[0.00000024 0.00000106 0.00000266 0.00329963 0.0002692  0.00001519
  0.00000005 0.00017251 0.00036265 0.9958768 ]
 [0.0000126  0.00001288 0.00002194 0.00050171 0.0294322  0.0024302
  0.00002043 0.00118914 0.00033697 0.966042  ]
 [0.02708253 0.00004767 0.00098977 0.00018168 0.01046194 0.00049998
  0.00001005 0.02793142 0.00042748 0.93236744]
 [0.00000756 0.00002098 0.00008155 0.00004344 0.00000212 0.0000143
  0.0000077  0.00000039 0.9997968  0.00002517]
 [0.00000551 0.00098367 0.00011048 0.00090309 0.95970374 0.0033097
  0.00006785 0.00511017 0.00188799 0.02791776]
 [0.00461162 0.00018102 0.15369849 0.00007356 0.02823423 0.0006634
  0.80148727 0.00012584 0.00059881 0.01032578]
 [0.00000104 0.00001165 0.00087681 0.00141926 0.00000293 0.00000021
  0.         0.9976088  0.00007685 0.00000243]
 [0.00016335 0.00000015 0.00027514 0.0001372  0.00000009 0.00000461
  0.00000886 0.00000003 0.99939644 0.00001424]
 [0.00000339 0.9993819  0.00037106 0.00000196 0.0000

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-06-21-11:19:46
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-40000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-06-21-11:19:47
INFO:tensorflow:Saving dict for global step 40000: accuracy = 0.9799, global_step = 40000, loss = 0.06454317
INFO:tensorflow:Saving 'checkpoint_path' summary for global step 40000: /tmp/mnist_convnet_model/model.ckpt-40000
{'accuracy': 0.9799, 'loss': 0.06454317, 'global_step': 40000}


SystemExit: ignored

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:2890: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [0]:
from google.colab import files
files.download("model.ckpt")

FileNotFoundError: ignored

In [0]:
from google.colab import files
files.download("/tmp/mnist_convnet_model/model.ckpt-40000")

FileNotFoundError: ignored